# rf603_multicpu
Likelihood and minimization: setting up a multi-core parallelized unbinned maximum likelihood fit




**Author:** Wouter Verkerke  
<i><small>This notebook tutorial was automatically generated with <a href= "https://github.com/root-project/root/blob/master/documentation/doxygen/converttonotebook.py">ROOTBOOK-izer</a> from the macro found in the ROOT repository  on Wednesday, April 17, 2024 at 11:19 AM.</small></i>

In [1]:
%%cpp -d
#include "RooRealVar.h"
#include "RooDataSet.h"
#include "RooGaussian.h"
#include "RooPolynomial.h"
#include "RooAddPdf.h"
#include "RooProdPdf.h"
#include "TCanvas.h"
#include "TAxis.h"
#include "RooPlot.h"
using namespace RooFit;

Create 3D pdf and data
-------------------------------------------

Create observables

In [2]:
RooRealVar x("x", "x", -5, 5);
RooRealVar y("y", "y", -5, 5);
RooRealVar z("z", "z", -5, 5);

Create signal pdf gauss(x)*gauss(y)*gauss(z)

In [3]:
RooGaussian gx("gx", "gx", x, 0.0, 1.0);
RooGaussian gy("gy", "gy", y, 0.0, 1.0);
RooGaussian gz("gz", "gz", z, 0.0, 1.0);
RooProdPdf sig("sig", "sig", RooArgSet(gx, gy, gz));

Create background pdf poly(x)*poly(y)*poly(z)

In [4]:
RooPolynomial px("px", "px", x, RooArgSet(-0.1, 0.004));
RooPolynomial py("py", "py", y, RooArgSet(0.1, -0.004));
RooPolynomial pz("pz", "pz", z);
RooProdPdf bkg("bkg", "bkg", RooArgSet(px, py, pz));

Create composite pdf sig+bkg

In [5]:
RooRealVar fsig("fsig", "signal fraction", 0.1, 0., 1.);
RooAddPdf model("model", "model", RooArgList(sig, bkg), fsig);

Generate large dataset

In [6]:
std::unique_ptr<RooDataSet> data{model.generate({x, y, z}, 200000)};

input_line_52:2:2: warning: 'data' shadows a declaration with the same name in the 'std' namespace; use '::data' to reference this declaration
 std::unique_ptr<RooDataSet> data{model.generate({x, y, z}, 200000)};
 ^


Parallel fitting
-------------------------------

In parallel mode the likelihood calculation is split in N pieces,
that are calculated in parallel and added a posteriori before passing
it back to MINUIT.

Use four processes and time results both in wall time and CPU time

In [7]:
model.fitTo(*data, NumCPU(4), Timer(true), PrintLevel(-1));

input_line_53:2:15: error: reference to 'data' is ambiguous
 model.fitTo(*data, NumCPU(4), Timer(true), PrintLevel(-1));
              ^
input_line_52:2:30: note: candidate found by name lookup is 'data'
 std::unique_ptr<RooDataSet> data{model.generate({x, y, z}, 200000)};
                             ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^


Parallel MC projections
----------------------------------------------

Construct signal, total likelihood projection on (y,z) observables and likelihood ratio

In [8]:
RooAbsPdf *sigyz = sig.createProjection(x);
RooAbsPdf *totyz = model.createProjection(x);
RooFormulaVar llratio_func("llratio", "log10(@0)-log10(@1)", RooArgList(*sigyz, *totyz));

Calculate likelihood ratio for each event, define subset of events with high signal likelihood

In [9]:
data->addColumn(llratio_func);
std::unique_ptr<RooAbsData> dataSel{data->reduce(Cut("llratio>0.7"))};

input_line_58:2:2: error: reference to 'data' is ambiguous
 data->addColumn(llratio_func);
 ^
input_line_52:2:30: note: candidate found by name lookup is 'data'
 std::unique_ptr<RooDataSet> data{model.generate({x, y, z}, 200000)};
                             ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^
input_line_58:3:37: error: reference to 'data' is ambiguous
std::unique_ptr<RooAbsData> dataSel{data->red

Make plot frame and plot data

In [10]:
RooPlot *frame = x.frame(Title("Projection on X with LLratio(y,z)>0.7"), Bins(40));
dataSel->plotOn(frame);

input_line_60:2:3: error: use of undeclared identifier 'dataSel'
 (dataSel->plotOn(((*(RooPlot **)0x7fac9b572000))))
  ^
Error in <HandleInterpreterException>: Error evaluating expression (dataSel->plotOn(((*(RooPlot **)0x7fac9b572000))))
Execution of your code was aborted.


Perform parallel projection using MC integration of pdf using given input dataSet.
In this mode the data-weighted average of the pdf is calculated by splitting the
input dataset in N equal pieces and calculating in parallel the weighted average
one each subset. The N results of those calculations are then weighted into the
final result

Use four processes

In [11]:
model.plotOn(frame, ProjWData(*dataSel), NumCPU(4));

new TCanvas("rf603_multicpu", "rf603_multicpu", 600, 600);
gPad->SetLeftMargin(0.15);
frame->GetYaxis()->SetTitleOffset(1.6);
frame->Draw();

input_line_61:2:43: error: cannot initialize an array element of type 'void *' with an rvalue of type 'RooCmdArg (*)(Int_t, Int_t)' (aka 'RooCmdArg (*)(int, int)')
 model.plotOn(frame, ProjWData(*dataSel), NumCPU(4));
                                          ^~~~~~


Draw all canvases 

In [12]:
%jsroot on
gROOT->GetListOfCanvases()->Draw()